* [#7](https://github.com/salgo60/Offentliga-toaletter/issues/7)
* denna Notebook [7_toaletter_se](https://github.com/salgo60/Offentliga-toaletter/blob/main/Notebook/7_toaletter_se.ipynb)

In [1]:
import time
from datetime import datetime

now = datetime.now()
timestamp = now.timestamp()

start_time = time.time()
print("Start:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))



Start: 2026-01-23 13:35:04


In [2]:
Mapversion = "0.1"

In [3]:
from urllib.parse import quote
from html import escape

def build_toilet_popup(item, *, include_source=True):

    
    coords = item.get("coordinates") or {}
    lat = coords.get("lat")
    lon = coords.get("lng")

    if lat is None or lon is None:
        return None 

    name = item.get("name", "Offentlig toalett")
    category = item.get("category", "")
    rating = item.get("rating")
    reviews = item.get("reviews")

    address = item.get("address") or {}
    street = address.get("street", "")
    city = address.get("city", "")
    city_slug = address.get("citySlug")

    province = item.get("province") or {}
    province_slug = province.get("slug")

    slug = item.get("slug")
    google_maps = item.get("googleMapsLink") or f"https://maps.google.com/?q={lat},{lon}"

    # ---- Offentligatoalette.se-länk ----
    oa_url = None
    if province_slug and city_slug and slug:
        oa_url = f"https://www.offentligatoalette.se/{province_slug}/{city_slug}/{slug}/"

    # ---- OSM Note ----
    note_text = (
        f"Offentlig toalett enligt offentligatoalette.se. "
        f"Namn: {name}. "
        f"Adress: {street}, {city}. "
        f"Kategori: {category}."
    )
    note_url = (
        f"https://www.openstreetmap.org/note/new"
        f"#map=18/{lat}/{lon}&text={quote(note_text)}"
    )

    # ---- Verktyg / appar ----
    mapcomplete = f"https://mapcomplete.org/toilets.html?z=17&lat={lat}&lon={lon}"
    wheelmap = f"https://wheelmap.org/map#/?lat={lat}&lon={lon}&zoom=17"
    streetview = f"https://www.google.com/maps/@?api=1&map_action=pano&viewpoint={lat},{lon}"
    wikishootme = f"https://wikishootme.toolforge.org/#lat={lat}&lng={lon}&zoom=17"

    # ---- Snabbknappar ----
    menu_html = f"""
    <div style='margin-top:8px; text-align:center;'>
      <a href='{mapcomplete}' target='_blank'
         style='background:#34a853;color:white;padding:6px 10px;
                border-radius:6px;text-decoration:none;margin:2px;
                display:inline-block;font-size:13px;'>
         🚻 MapComplete
      </a>

      <a href='{wheelmap}' target='_blank'
         style='background:#7c3aed;color:white;padding:6px 10px;
                border-radius:6px;text-decoration:none;margin:2px;
                display:inline-block;font-size:13px;'>
         ♿ Wheelmap
      </a>

      <a href='{note_url}' target='_blank'
         style='background:#fbbc04;color:black;padding:6px 10px;
                border-radius:6px;text-decoration:none;margin:2px;
                display:inline-block;font-size:13px;'>
         📝 OSM Note
      </a>
    </div>
    """

    # ---- Fler verktyg ----
    tools_html = f"""
    <details style='margin-top:6px; text-align:center;'>
      <summary style='cursor:pointer;font-weight:bold;'>🔗 Fler kartverktyg</summary>
      <a href='https://www.openstreetmap.org/edit#map=18/{lat}/{lon}' target='_blank'>✏️ iD Editor</a><br>
      <a href='https://www.mapillary.com/app/?lat={lat}&lng={lon}&z=17' target='_blank'>🟢 Mapillary</a><br>
      <a href='{google_maps}' target='_blank'>🗺️ Google Maps</a><br>
      <a href='{streetview}' target='_blank'>👁️ Street View</a><br>
      <a href='{wikishootme}' target='_blank'>🧭 Wikishootme</a><br>
    </details>
    """

    source_html = ""
    if include_source:
        source_html = """
        <hr style="margin:6px 0;">
        <small>
          <b>Källa:</b>
          <a href="https://www.offentligatoalette.se/" target="_blank">
            offentligatoalette.se
          </a>
        </small>
        """

    rating_html = ""
    if rating is not None:
        rating_html = f"<b>Betyg:</b> {rating} ⭐ ({reviews} recensioner)<br>"

    oa_html = ""
    if oa_url:
        oa_html = f"""
        <b>Offentligatoalette.se:</b>
        <a href="{oa_url}" target="_blank">Visa sida</a><br>
        """

    popup_html = f"""
    <div style='font-family:Arial; font-size:13px; max-width:320px;'>
      <b>🚻 {escape(name)}</b><br>
      <b>Kategori:</b> {escape(category)}<br>
      <b>Adress:</b> {escape(street)}, {escape(city)}<br>
      {rating_html}
      {oa_html}
      📍 <a href='https://www.openstreetmap.org/?mlat={lat}&mlon={lon}#map=18/{lat}/{lon}'
            target='_blank'>{lat:.5f}, {lon:.5f}</a><br>

      {menu_html}
      {tools_html}
      {source_html}
    </div>
    """

    return {
        "lat": lat,
        "lon": lon,
        "name": name,
        "html": popup_html
    }


In [4]:
from html import escape
import folium
import requests

url = "https://gist.githubusercontent.com/salgo60/37362174f233af109618296a13f36ef6/raw/20e1ea2963edf72f9cc39c66228d561f64472887/toilets.json"
data = requests.get(url).json()

m = folium.Map(location=[59.3, 18.3], zoom_start=6)
fg = folium.FeatureGroup(name="Toaletter")

for item in data:
    coords = item.get("coordinates") or {}
    lat = coords.get("lat")
    lng = coords.get("lng")

    if lat is None or lng is None:
        continue

    name = item.get("name", "Okänt namn")
    category = item.get("category", "")
    rating = item.get("rating")
    reviews = item.get("reviews")
    timing = item.get("timing", "")
    closed_on = item.get("closedOn", "")
    image = item.get("image", "")
    gmaps = item.get("googleMapsLink", "")

    address = item.get("address", {})
    city = address.get("city", "")
    street = address.get("street", "")

    province = item.get("province") or {}
    province_slug = province.get("slug")
    city_slug = address.get("citySlug")
    slug = item.get("slug")

    oa_url = None
    if province_slug and city_slug and slug:
        oa_url = f"https://www.offentligatoalette.se/{province_slug}/{city_slug}/{slug}/"

    # HTML-popup
    result = build_toilet_popup(item)
    if not result:
        continue
    
    folium.Marker(
        location=[result["lat"], result["lon"]],
        popup=folium.Popup(result["html"], max_width=350),
        tooltip=result["name"],
        icon=folium.Icon(icon="info-sign")
    ).add_to(fg)

fg.add_to(m)
#folium.LayerControl(collapsed=False).add_to(m)



In [5]:
from datetime import datetime, timezone

generated_at = datetime.now(timezone.utc).strftime("%Y-%m-%d %H:%M UTC")

legend_html = f"""
<div style="
    position: fixed;
    bottom: 30px;
    left: 30px;
    width: 320px;
    z-index: 10000;
    font-size: 12px;
">

  <!-- Header / Toggle -->
  <div onclick="var c=document.getElementById('legend-content');
                c.style.display = (c.style.display === 'none') ? 'block' : 'none';"
       style="
        cursor: pointer;
        background: white;
        padding: 8px;
        border: 2px solid #ccc;
        border-radius: 6px 6px 0 0;
        font-weight: bold;
       ">
    offentligatoalette.se – v{Mapversion}
    <span style="float:right;">▼</span>
  </div>

  <!-- Collapsible content -->
  <div id="legend-content" style="
        display: none;
        background: white;
        padding: 10px;
        border: 2px solid #ccc;
        border-top: none;
        border-radius: 0 0 6px 6px;
  ">

    <small><i>Karta genererad: {generated_at}</i></small><br><br>

    <b>Syfte</b><br>
    Se hur offentligatoalette har för kvalitet... 
    – se issue
    (<i>amenity=toilets</i>).<br><br>

    <b>Mer info</b><br>
    • <a href="https://github.com/salgo60/Offentliga-toaletter/issues/7" target="_blank">
      GitHub Issue #7
    </a><br>
    • <a href="https://www.offentligatoalette.se" target="_blank">
      www.offentligatoalette.se
    <br /><br />...  
    </a>

  </div>
</div>
"""


In [6]:
m.get_root().html.add_child(folium.Element(legend_html))
folium.LayerControl(collapsed=False).add_to(m)

In [7]:
m.save("toaletter_se_karta.html")

In [8]:
m

In [9]:
 # End timer and calculate duration
end_time = time.time()
elapsed_time = end_time - start_time# Bygg audit-lager för den här etappen

# Print current date and total time
print("Date:", datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
print("Total time elapsed: {:.2f} seconds".format(elapsed_time))

Date: 2026-01-23 13:35:07
Total time elapsed: 3.22 seconds
